# 3．流れのシミュレーション

## まとめと演習

### 1. Cavity 流れ

#### 問題

隙間がないように上面を平板で塞いだ一辺の長さが $L$ のコの字型の溝（下は断面図）の中で，密度 $\rho$，粘度 $\mu$ の非圧縮ニュートン流体が静止状態にある．いま，時刻 $t=0$ において図のように一定速度 $V$ で平板のスライドを開始し，$t>0$ で同じ速度を保持するものとする．溝中の流速ベクトル ${\bf u}({\bf x},t)$ を求めよ．

<img src="fig/Cavity.png">

#### 無次元化

- Reynolds number 
$${\rm Re}=\frac{\rho V L}{\mu}$$

- Reduced fluid velocity
$${\bf u^*}({\bf x^*},t^*)=\frac{1}{V}\ {\bf u}({\bf x},t)$$

- Reduced position
$${\bf x^*}=\frac{1}{L}\ {\bf x}$$

- Reduced time
$$t^*=\frac{V}{L}\ t$$




#### Code examples

##### 0. Import libraries

In [1]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
import sys,random

##### 1. MAC method

- In case of overflow error, reduce `dt`

- This sample simulation takes about 10 minuets using a standard PC. 

In [ ]:
#Reynolds number, Re = 1 - 10000)
Re = 1.0
####
Nx, Ny = 23, 23
u = np.zeros([Nx, Ny])
v = np.zeros([Nx, Ny])
p = np.zeros([Nx, Ny])
r = np.zeros([Nx, Ny])
d = np.zeros([Nx, Ny])
Mx, My = 20, 20
I21, J21 = Mx + 1, My + 1
dt = 0.00025*np.sqrt(Re)
print("Re =",Re)
print("dt =",dt)
Lm = 4000
Km = 50

us = np.zeros([Nx, Ny, Lm])
vs = np.zeros([Nx, Ny, Lm])
ps = np.zeros([Nx, Ny, Lm])
Dx = 1.0/float(I21 - 3)
Dy = 1.0/float(J21 - 3)
xd = 1.0/Dx
yd = 1.0/Dy
xdh = 0.5*xd
ydh = 0.5*yd
td = 1.0/dt
R1 = 1.0/Re
I20 = I21 - 1
I19 = I21 - 2
J20 = J21 - 1
J19 = J21 - 2
A1  = 0.5*Dy*Dy/(Dx*Dx + Dy*Dy)
A2  = 0.5*Dx*Dx/(Dx*Dx + Dy*Dy)
A3  = 0.5*Dy*Dy/(1.0 + Dy*Dy/(Dx*Dx))
eps = 0.001

x = np.zeros([Nx])
y = np.zeros([Ny])
for i in range(Nx):
    x[i]=Dx*(i-2)
for j in range(Ny):
    y[j]=Dy*(j-2)

#boundary conditions for u and v
for i in range(1, I21+1):
    u[i, J20] = 1.0
    v[i, J21] = v[i, J19]
    v[i, J20] = 0.0
    v[i, 1] = v[i, 3]
    v[i, 2] = 0.0
    u[i, 1] = - u[i, 2]    
for j in range(1, J21+1):
    u[I21, j] = u[I19, j]
    u[I20, j] = 0.0
    v[I20, j] = - v[I19, j]
    u[1, j] = u[3, j]
    u[2, j] = 0.0
    v[1, j] = - v[2, j]

#main iteration for t
for t in range(1, Lm+1):
    
    #calc. Right-hand-side of Poisson eq
    divv = 0.0
    for j in range(2, J19+1):
        for i in range(2, I19+1):
            u1 = (u[i+1, j] - u[i, j])*xd
            v2 = (v[i, j+1] - v[i, j])*yd
            d[i, j] = u1 + v2
            divv = divv + np.abs(u1 + v2)
            ua = 0.25*(u[i, j] + u[i+1, j] + u[i+1, j+1] + u[i, j+1])
            ub = 0.25*(u[i, j] + u[i+1, j] + u[i+1, j-1] + u[i, j-1])
            va = 0.25*(v[i, j] + v[i, j+1] + v[i+1, j+1] + v[i+1, j])
            vb = 0.25*(v[i, j] + v[i, j+1] + v[i-1, j+1] + v[i-1, j])
            r[i, j] = - u1*u1- 2.0*(ua - ub)*(va -vb)*xd*yd - v2*v2 + td*(u1 + v2)
            
    #solve Poisson eq with SOR method
    for k in range(1, Km+1):
        G2 = 0.0
        for j in range(1, J21+1):
            p[1, j] = p[2, j]
            p[I20, j] = p[I19, j]
        for i in range(1, I21+1):
            p[i, 1] = p[i, 2]
            p[i, J20] = p[i, J19]
            
        for j in range(2, J19+1):
            for i in range(2, I19+1):
                uli = A1*(p[i+1, j] + p[i-1, j]) + A2*(p[i, j+1] + p[i, j-1]) - A3*r[i, j] - p[i, j]
                G2 = G2 + uli*uli
                p[i, j] = uli + p[i, j]
                
        if(G2 <= eps):
            break            
    sys.stdout.write("\r%d" %t +" / "+"%d" % Lm +"  "+"%d" % k +"  "+"%e" % G2 +"  "+"%e" % eps+"    ")
    sys.stdout.flush()
        
    #integrate Navier-Stokes eq n -> n+1
    for j in range(2, J19+1):
        for i in range(3, I19+1):
            v1 = 0.25*(v[i, j] + v[i, j+1] + v[i-1, j+1] + v[i-1, j])
            un = u[i, j]*(u[i+1, j] - u[i-1, j])*xdh + v1*(u[i, j+1] - u[i, j-1])*ydh
            uv = (u[i+1, j] - 2.0*u[i, j] + u[i-1, j])*xd*xd + (u[i, j+1] - 2.0*u[i, j] + u[i, j-1])*yd*yd
            d[i, j] = u[i, j] + dt*(- un - (p[i, j] - p[i-1, j])*xd + R1*uv)
    for j in range(3, J19+1):
        for i in range(2, I19+1):
            u1 = 0.25*(u[i, j] + u[i+1, j] + u[i+1, j-1] + u[i, j-1])
            vn = u1*(v[i+1, j] - v[i-1, j])*xdh + v[i, j]*(v[i, j+1] - v[i, j-1])*ydh
            vv = (v[i+1, j] - 2.0*v[i, j] + v[i-1, j])*xd*xd + (v[i, j+1] - 2.0*v[i, j] + v[i, j-1])*yd*yd
            r[i, j] = v[i, j] + dt*(- vn - (p[i, j] - p[i, j-1])*yd + R1*vv)    
    for j in range(2, J19+1):
        for i in range(3, I19+1):
            u[i, j] = d[i, j]
    for j in range(3, J19+1):
        for i in range(2, I19+1):
            v[i, j] = r[i, j]

    #boundary conditions for u and v
    for i in range(1, I21+1):
        u[i, J20] = 1.0
        v[i, J21] = v[i, J19]
        v[i, J20] = 0.0
        v[i, 1] = v[i, 3]
        v[i, 2] = 0.0
        u[i, 1] = - u[i, 2]    
    for j in range(1, J21+1):
        u[I21, j] = u[I19, j]
        u[I20, j] = 0.0
        v[I20, j] = - v[I19, j]
        u[1, j] = u[3, j]
        u[2, j] = 0.0
        v[1, j] = - v[2, j]

    for j in range(Ny):
        for i in range(Nx):
            us[i,j,t-1]=u[i,j]
            vs[i,j,t-1]=v[i,j]
            ps[i,j,t-1]=p[i,j]
            
print("finished")

##### 2. Plot velocity vectors and stream lines

In [ ]:
#make plot

plt.figure(figsize = (20, 3.5))

ns=1
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(151)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
plt.quiver(x,y,u.T,v.T, color='red', zorder = 10, width = 0.005, scale = 4, pivot='mid')
plt.streamplot(x,y,u.T,v.T)
plt.xlim(x[2],x[20])
plt.ylim(y[2],y[20])
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

ns=int(Lm/4*1)
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(152)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
plt.quiver(x,y,u.T,v.T, color='red', zorder = 10, width = 0.005, scale = 4, pivot='mid')
plt.streamplot(x,y,u.T,v.T)
plt.xlim(x[2],x[20])
plt.ylim(y[2],y[20])
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

ns=int(Lm/4*2)
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(153)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
plt.quiver(x,y,u.T,v.T, color='red', zorder = 10, width = 0.005, scale = 4, pivot='mid')
plt.streamplot(x,y,u.T,v.T)
plt.xlim(x[2],x[20])
plt.ylim(y[2],y[20])
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

ns=int(Lm/4*3)
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(154)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
plt.quiver(x,y,u.T,v.T, color='red', zorder = 10, width = 0.005, scale = 4, pivot='mid')
plt.streamplot(x,y,u.T,v.T)
plt.xlim(x[2],x[20])
plt.ylim(y[2],y[20])
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

ns=Lm
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(155)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
plt.quiver(x,y,u.T,v.T, color='red', zorder = 10, width = 0.005, scale = 4, pivot='mid')
plt.streamplot(x,y,u.T,v.T)
plt.xlim(x[2],x[20])
plt.ylim(y[2],y[20])
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

### 2. 楕円柱の周囲の流れ

#### 問題

長軸の長さが $L$ の楕円柱の障害物（下は断面図）が，密度 $\rho$，粘度 $\mu$ の静止した非圧縮ニュートン流体中にある．いま時刻 $t=0$ において，障害物から十分に遠い場所で一様速度 $V$ に流体を瞬間的に加速し，$t>0$ で同じ一様流速を保持するものとする．障害物の周りの流速ベクトル ${\bf u}({\bf x},t)$ を求めよ．

<img src="fig/Obstacle.png">

#### 無次元化

- Reynolds number 
$${\rm Re}=\frac{\rho V L}{\mu}$$

- Reduced fluid velocity
$${\bf u^*}({\bf x^*},t^*)=\frac{1}{V}\ {\bf u}({\bf x},t)$$

- Reduced position
$${\bf x^*}=\frac{1}{L}\ {\bf x}$$

- Reduced time
$$t^*=\frac{V}{L}\ t$$


#### Code examples

##### 1. MAC  method

- In case of overflow error, reduce `dt`

- This sample simulation takes about 30-60 minuets using a standard PC. 

In [ ]:
#Reynolds number, Re = 1 - 500)
Re = 1.0
####
#grid making
igr, ityp = 0, 1
Jmax = 62
Kmax = 31
AA  = 0.75
BB = 1.0
HH = 0.025
RA  = 1.15
RR = np.zeros(Kmax+1)
RR[1] = 1.0
for k in range(2, Kmax+1):
    RR[k]  = RR[k-1] + HH*RA**(k-1)

x, y = np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1])
for k in range(1, Kmax+1):
    for j in range(1, Jmax+1):
        TT  =2.0*np.pi * float(j-2)/float(Jmax-2)
        BC = BB + (AA - BB)*float(k-1)/float(Kmax-1)
        x[j, k] = AA*RR[k]*np.cos(TT)
        y[j, k] = BC*RR[k]*np.sin(TT)
        
#input data
Jm = Jmax - 1
Km = Kmax - 1
nsteps = 4000
istep0 = 20
#dt = 0.0004
dt = 0.0001*np.sqrt(Re)
print("Re =",Re)
print("dt =",dt)
eps = 0.001
const = 1.0
Rei = 1.0/Re
dti = 1.0/dt

#caluculating metrics
xx, xy, yx, yy = np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1])
c1, c2, c3 = np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1])
c4, c5, aj= np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1])

for k in range(1, Kmax+1):
    for j in range(1, Jmax+1):
        
        if(k == 1):
            xe = 0.5*(- x[j, 3] + 4.0*x[j, 2] - 3.0*x[j, 1])
            ye = 0.5*(- y[j, 3] + 4.0*y[j, 2] - 3.0*y[j, 1])
        elif(k == Kmax):
            xe = 0.5*(x[j, Kmax-2] - 4.0*x[j, Kmax-1] + 3.0*x[j, Kmax])
            ye = 0.5*(y[j, Kmax-2] - 4.0*y[j, Kmax-1] + 3.0*y[j, Kmax])
        else:
            xe = 0.5*(x[j, k+1] - x[j, k-1])
            ye = 0.5*(y[j, k+1] - y[j, k-1])
            
        if(j == 1):
            xxi = 0.5*(- x[3, k] + 4.0*x[2, k] - 3.0*x[1, k])
            yxi = 0.5*(- y[3, k] + 4.0*y[2, k] - 3.0*y[1, k])
            if(ityp == 1):
                xxi = 0.5*(x[2, k] - x[Jmax -2, k])
                yxi = 0.5*(y[2, k] - y[Jmax -2, k])
        elif(j == Jmax):
            xxi = 0.5*(x[Jmax-2, k] - 4.0*x[Jmax-1, k] + 3.0*x[Jmax, k])
            yxi = 0.5*(y[Jmax-2, k] - 4.0*y[Jmax-1, k] + 3.0*y[Jmax, k])
            if(ityp == 1):
                xxi = 0.5*(x[3, k] - x[Jmax -1, k])
                yxi = 0.5*(y[3, k] - y[Jmax -1, k])
        else:
            xxi = 0.5*(x[j+1, k] - x[j-1, k])
            yxi = 0.5*(y[j+1, k] - y[j-1, k])   
            
        if(ityp == 1 and j ==1):
            xxi = 0.5*(x[j+1, k] - x[Jm -1, k])
            yxi = 0.5*(y[j+1, k] - y[Jm -1, k])
            
        if(ityp == 1 and j == Jmax):
            xxi = 0.5*(x[3, k] - x[j-1, k])
            yxi = 0.5*(y[3, k] - y[j-1, k])
            
        ajj = xxi*ye - xe*yxi
        xx[j, k] = ye/ajj
        yx[j, k] = - yxi/ajj
        xy[j, k] = - xe/ajj
        yy[j, k] = xxi/ajj
        aj[j, k] = ajj
        
for k in range(1, Kmax+1):
    for j in range(1, Jmax+1):
        c1[j, k] = xx[j, k]**2 + xy[j, k]**2
        c3[j, k] = yx[j, k]**2 + yy[j, k]**2
        c2[j, k] = 2.0*(xx[j, k]*yx[j, k] + xy[j, k]*yy[j, k])
        
for k in range(2, Km+1):
    for j in range(2, Jm+1):
        c77 = xx[j, k]*(xx[j+1, k] - xx[j-1, k]) + yx[j, k]*(xx[j, k+1] - xx[j, k-1]) + xy[j, k]*(xy[j+1, k] - xy[j-1, k]) + yy[j, k]*(xy[j, k+1] - xy[j, k-1])
        c88 = xx[j, k]*(yx[j+1, k] - yx[j-1, k]) + yx[j, k]*(yx[j, k+1] - yx[j, k]) + xy[j, k]*(yy[j+1, k] - yy[j-1, k]) + yy[j, k]*(yy[j, k+1] - yy[j, k-1])
        c4[j, k] = c77*0.5
        c5[j, k] = c88*0.5
            
#init condtion
alp = 0.
TTT = alp*np.pi/180.0
u, v, p = np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1])
us, vs, ps = np.zeros([Jmax+1, Kmax+1, nsteps]), np.zeros([Jmax+1, Kmax+1, nsteps]), np.zeros([Jmax+1, Kmax+1, nsteps])
q, d  = np.zeros([Jmax+1, Kmax+1]), np.zeros([Jmax+1, Kmax+1])
random.seed(1)
for k in range(1, Kmax+1):
    for j in range(1, Jmax+1):
        u[j, k] = np.cos(TTT)+0.05*(random.random()-0.5)
        v[j, k] = np.sin(TTT)+0.05*(random.random()-0.5)
        p[j, k] = 0.0 - 0.5*(u[j, k]**2 + v[j, k]**2)

#main
for n in range(1, nsteps+1):
    #calculating RHS of poisson eq
    for k in range(2, Km+1):
        for j in range(2, Jm+1):
            uxd = xx[j, k]*(u[j+1, k] - u[j-1, k]) + yx[j, k]*(u[j, k+1] - u[j, k-1])
            uyd = xy[j, k]*(u[j+1, k] - u[j-1, k]) + yy[j, k]*(u[j, k+1] - u[j, k-1])
            vxd = xx[j, k]*(v[j+1, k] - v[j-1, k]) + yx[j, k]*(v[j, k+1] - v[j, k-1])
            vyd = xy[j, k]*(v[j+1, k] - v[j-1, k]) + yy[j, k]*(v[j, k+1] - v[j, k-1])
            q[j, k] = - 0.25*(uxd*uxd + 2.0*uyd*vxd + vyd*vyd) + 0.5*(uxd + vyd)*dti
            
    err = 0.0
    for i in range(1, istep0+1):
        #calculating Pressure 
        for k in range(2, Km+1):
            for j in range(2, Jm+1):
                cc = 0.5/(c1[j, k] + c3[j, k])
                pa1 = c1[j, k]*(p[j+1, k] + p[j-1, k]) + c3[j, k]*(p[j, k+1] + p[j, k-1]) + 0.25*c2[j, k]*(p[j+1, k+1] - p[j-1, k+1] - p[j+1, k-1] + p[j-1, k-1])
                pa2 = 0.5*c4[j, k]*(p[j+1, k] - p[j-1, k]) + 0.5*c5[j, k]*(p[j, k+1] - p[j, k-1])
                pa = pa1 + pa2
                pp = (pa - q[j, k])*cc
                err = err + (pp - p[j, k])**2
                p[j, k] = p[j, k]*(1.0 - const) + pp*const
                
        #Pressure boundary condition
        for j in range(2, Jm+1):
            ul = 0.5*c2[j, 1]*(u[j+1, 2] - u[j-1, 2]) + c5[j, 1]*u[j, 1]
            vl = 2.0*c3[j, 1]*v[j, 2]
            p[j, 1] = p[j, 2] - Rei*aj[j, 1]*(xx[j, 1]*vl - xy[j, 2]*ul)
            p[j, Kmax] = - 0.5*(u[j, Kmax]**2 + v[j, Kmax]**2)
            
        if(ityp == 1):
            for k in range(1, Kmax+1):
                p[1, k] = p[Jm, k]
                p[Jmax, k] = p[2, k]
        else:
            for k in range(1, Kmax+1):
                p[1, k] = p[2, k]
                p[Jmax, k] = p[Jm, k]
        
        #print(err)
        if(err < eps ):
            count = i
            break
    sys.stdout.write("\r%d" %n +" / "+"%d" % nsteps +"  "+"%d" % i +"  "+"%e" % err +"  "+"%e" % eps+"    ")
    sys.stdout.flush()
    
    #convergence check
#    print(n,err, i)
    
    #calculating velocity
    for k in range(2, Km+1):
        for j in range(2, Jm+1):
            unl1 = xx[j, k]*(u[j+1, k]**2 - u[j-1, k]**2)*0.5 + yx[j, k]*(u[j, k+1]**2 - u[j, k-1]**2)*0.5
            unl2 = xy[j, k]*(u[j+1, k]*v[j+1, k] - u[j-1, k]*v[j-1, k])*0.5 + yy[j, k]*(u[j, k+1]*v[j, k+1] - u[j, k-1]*v[j, k-1])*0.5
            unl = unl1 + unl2
            vnl1 = xx[j, k]*(u[j+1, k]*v[j+1, k] - u[j-1, k]*v[j-1, k])*0.5 + yx[j, k]*(u[j, k+1]*v[j, k+1] - u[j, k-1]*v[j, k-1])*0.5
            vnl2 = xy[j, k]*(v[j+1, k]**2 - v[j-1, k]**2)*0.5 + yy[j, k]*(v[j, k+1]**2 - v[j, k-1]**2)*0.5
            vnl = vnl1 + vnl2
            uvs1 = c1[j, k]*(u[j+1, k] - 2.0*u[j, k] + u[j-1, k]) + c2[j, k]*(u[j+1, k+1] - u[j+1, k-1] - u[j-1, k+1] + u[j-1, k-1])*0.25
            uvs2 = c3[j,k]*(u[j, k+1] - 2.0*u[j, k] + u[j, k-1]) + 0.5*c4[j, k]*(u[j+1, k] - u[j-1, k]) + 0.5*c5[j, k]*(u[j, k+1] - u[j, k-1])
            uvs = uvs1 + uvs2
            vvs1 = c1[j, k]*(v[j+1, k] - 2.0*v[j, k] + v[j-1, k]) + c2[j, k]*(v[j+1, k+1] - v[j+1, k-1] - v[j-1, k+1] + v[j-1, k-1])*0.25
            vvs2 = c3[j,k]*(v[j, k+1] - 2.0*v[j, k] + v[j, k-1]) + 0.5*c4[j, k]*(v[j+1, k] - v[j-1, k]) + 0.5*c5[j, k]*(v[j, k+1] - v[j, k-1])
            vvs = vvs1 + vvs2
            d[j, k] = u[j, k] + dt*(- unl - 0.5*xx[j, k]*(p[j+1, k] - p[j-1, k]) - 0.5*yx[j, k]*(p[j, k+1] - p[j, k-1]) + Rei*uvs)
            q[j, k] = v[j, k] + dt*(- vnl - 0.5*xy[j, k]*(p[j+1, k] - p[j-1, k]) - 0.5*yy[j, k]*(p[j, k+1] - p[j, k-1]) + Rei*vvs)
            
    for k in range(2, Km+1):
        for j in range(2, Jm+1):
            u[j, k] = d[j, k]
            v[j, k] = q[j, k]

    #boundary condition
    TTT  = alp*np.pi/180.0
    for j in range(1, Jmax+1):
        u[j, 1] = 0.0
        v[j, 1] = 0.0
        u[j, Kmax] = np.cos(TTT)
        v[j, Kmax] = np.sin(TTT)
        
    if(ityp == 1):
        for k in range(1, Kmax+1):
            u[1, k] = u[Jm, k]
            v[1, k] = v[Jm, k]
            u[Jmax, k] = u[2, k]
            v[Jmax, k] = v[2, k]
    else:
        for k in range(1, Kmax+1):
            u[1, k] = u[2, k]
            v[1, k] = 0.0
            u[Jmax, k] = u[Jm, k]
            v[Jmax, k] = 0.0

    for k in range(Kmax):
        for j in range(Jmax):
            us[j,k,n-1]=u[j,k]
            vs[j,k,n-1]=v[j,k]
            ps[j,k,n-1]=p[j,k]

print("finished")

##### 2. Plot velocity vectors

In [ ]:
#make plot

plt.figure(figsize = (20, 3.5))

ns=1
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(151)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
start, finish = 1, 63
plt.quiver(x[start:finish, start:finish], y[start:finish, start:finish], u[start:finish, start:finish], v[start:finish, start:finish], scale = 20, pivot='mid')
plt.xlim(-3, 3)
plt.ylim(-3, 3)
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

ns=int(nsteps/4*1)
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(152)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
start, finish = 1, 63
plt.quiver(x[start:finish, start:finish], y[start:finish, start:finish], u[start:finish, start:finish], v[start:finish, start:finish], scale = 20, pivot='mid')
plt.xlim(-3, 3)
plt.ylim(-3, 3)
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

ns=int(nsteps/4*2)
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(153)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
start, finish = 1, 63
plt.quiver(x[start:finish, start:finish], y[start:finish, start:finish], u[start:finish, start:finish], v[start:finish, start:finish], scale = 20, pivot='mid')
plt.xlim(-3, 3)
plt.ylim(-3, 3)
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

ns=int(nsteps/4*3)
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(154)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
start, finish = 1, 63
plt.quiver(x[start:finish, start:finish], y[start:finish, start:finish], u[start:finish, start:finish], v[start:finish, start:finish], scale = 20, pivot='mid')
plt.xlim(-3, 3)
plt.ylim(-3, 3)
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

ns=nsteps
tplot=dt*(ns)
u=us[:,:,ns-1].copy()
v=vs[:,:,ns-1].copy()
plt.subplot(155)
plt.title("Re="+str(Re)+":   "+"t="+str(tplot))
start, finish = 1, 63
plt.quiver(x[start:finish, start:finish], y[start:finish, start:finish], u[start:finish, start:finish], v[start:finish, start:finish], scale = 20, pivot='mid')
plt.xlim(-3, 3)
plt.ylim(-3, 3)
plt.tick_params(labelbottom='off')
plt.tick_params(labelleft='off')

## 課題

### 1. 
- MAC法を用いて作成した「Cavity流れ」のサンプルプログラムを用いて, キャビティー内の流れの様子がレイノルズ数とともにどのように変わるかを考察せよ.

### 2.
- MAC法を用いて作成した「楕円柱の周囲の流れ」のサンプルプログラムを用いて, 楕円柱周りの流れの様子がレイノルズ数とともにどのように変わるかを考察せよ.

### 3. (アドバンストな自習問題)
- MAC法を用いて作成した「Cavity流れ」のサンプルプログラムを，プロジェクション法に書き直せ.


